In [22]:
%load_ext autoreload
%autoreload 1
%aimport seir.cross_beta

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


[autoreload of seir.cross_beta failed: Traceback (most recent call last):
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/site-packages/IPython/extensions/autoreload.py", line 245, in check
    superreload(m, reload, self.old_objects)
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/site-packages/IPython/extensions/autoreload.py", line 394, in superreload
    module = reload(module)
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/imp.py", line 314, in reload
    return importlib.reload(module)
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/importlib/__init__.py", line 169, in reload
    _bootstrap._exec(spec, module)
  File "<frozen importlib._bootstrap>", line 630, in _exec
  File "<frozen importlib._bootstrap_external>", line 728, in exec_module
  File "<frozen importlib._bootstrap>", line 219, in _call_with_frames_removed
  File "/Users/robertperrotta/PycharmProjects/covid-binder/seir/cross_beta.py",

In [23]:
import seir.cross_beta

In [24]:
from itertools import product
import pickle

import holoviews as hv
import numpy as np
import pandas as pd
import pymc3 as pm

In [25]:
hv.notebook_extension('bokeh', logo=False)
%opts Overlay [aspect=5/3, responsive=True]

In [26]:
with open('tmp.pkl', 'rb') as f:
    kwargs = pickle.load(f)
print({k: np.array(v).shape for k, v in kwargs.items()})
print({k: np.array(v).mean() for k, v in kwargs.items()})

{'i0': (), 'e0': (3,), 'beta': (1, 4, 3, 1, 1, 1, 1), 'beta_detected_ratio': (1, 4, 3, 1, 1, 1, 1), 'beta_era_ratios': (1, 1, 1, 1, 1, 1, 2), 'sigma': (4, 3, 1, 1, 1, 1), 'theta': (5, 1, 1, 1, 1, 1), 'gamma': (5, 3, 1, 1, 1, 1), 'mu': (3, 3, 2, 1, 1, 1)}
{'i0': 22.371910404835926, 'e0': 9.212842348518723, 'beta': -3.083021903764631, 'beta_detected_ratio': -3049.088666662443, 'beta_era_ratios': 4.702688478200857, 'sigma': -2.749014636387555, 'theta': -4.586603736301138, 'gamma': -4.242741818432618, 'mu': -4.8497449632283}


In [27]:
y = seir.cross_beta.ng_deterministic_ode(**kwargs)
y.shape

(6, 3, 2, 2, 2, 457)

In [28]:
T = seir.cross_beta.T
POPULATION = seir.cross_beta.POPULATION
lombardia = seir.cross_beta.lombardia

In [29]:
def plot(kwargs):
    y = seir.cross_beta.ng_deterministic_ode(**kwargs)

    T = seir.cross_beta.T
    lombardia = seir.cross_beta.lombardia

    plot = hv.Overlay([
        hv.Curve((T, np.sum(yi, axis=(0, 1, 2, 3, 4))), 'date', 'Count', label=name) *
        hv.Scatter(lombardia, 'data', name, label=name).options(size=6, alpha=0.4)
        for yi, name in [
            (y[1:, :, 1:, :, :], 'totale_casi'),
            (y[1:, :, 1:, :1, :1], 'totale_positivi'),
            (y[:, :, 1:, :, 1:], 'deceduti'),
            (y[2:-2, :, 1:, :1, :1], 'isolamento_domiciliare'),
            (y[-2:-1, :, 1:, :1, :1], 'ricoverati_con_sintomi'),
            (y[-1:, :, 1:, :1, :1], 'terapia_intensiva'),
            (y[-2:, :, 1:, 1:, :1], 'dimessi_guariti'),
        ]
    ] +
    [
        hv.Curve((T, np.sum(y[1:, :, :1, :, :], axis=(0, 1, 2, 3, 4))), 'date', 'Count', label='hidden cases')
        .options(line_dash='dotted'),
        hv.Curve((T, np.sum(y[1:, :, :, :, :], axis=(0, 1, 2, 3, 4))), 'date', 'Count', label='all cases')
        .options(line_dash='dotted'),
    ]).options(aspect=2, legend_position='top_left')
    
    return (
        plot +
        plot.options(logy=True, show_legend=False).redim.range(Count=(1, None)) +
        hv.Overlay([
            hv.Curve((T, yi.sum(axis=(0, 1, 2, 3))), 'date', 'count', label=name) *
            hv.Scatter(seir.cross_beta.deaths, 'day', name, label=name).options(size=6, alpha=0.4)
            for yi, name in [
                (y[:, 0, 1:, :, 1:], '0-50'),
                (y[:, 1, 1:, :, 1:], '51-70'),
                (y[:, 2, 1:, :, 1:], '>70'),
            ]
        ], group='deaths').options(logy=True).redim.range(count=(1, None)) +
        hv.Overlay([
            hv.Curve((T, 100 * yi), 'date', '% lethality by age', label=name) *
            hv.Scatter((seir.cross_beta.lethality['day'], x), label=name).options(size=6, alpha=0.4)
            for yi, x, name in [
                (y[:, 0, 1, :, 1].sum(axis=(0, 1)) / y[:, 0, 1, :, :].sum(axis=(0, 1, 2)), seir.cross_beta.data_lethality[0], '0-50'),
                (y[:, 1, 1, :, 1].sum(axis=(0, 1)) / y[:, 1, 1, :, :].sum(axis=(0, 1, 2)), seir.cross_beta.data_lethality[1], '51-70'),
                (y[:, 2, 1, :, 1].sum(axis=(0, 1)) / y[:, 2, 1, :, :].sum(axis=(0, 1, 2)), seir.cross_beta.data_lethality[2], '>70'),
            ]
        ], group='% lethality by age') +
        hv.Overlay([
            hv.Curve((T, 100 * yi.sum(axis=(0, 1, 2, 3)) / y[2:, :, 1:, :1, :1].sum(axis=(0, 1, 2, 3, 4))),
                     'date', '% by severity', label=name) *
            hv.Scatter(seir.cross_beta.severity, 'day', name, label=name).options(size=6, alpha=0.4)
            for yi, name in [
                (y[2, :, 1:, :1, :1], 'asintomatico'),
                (y[3, :, 1:, :1, :1], 'pauci-lieve'),
                (y[4, :, 1:, :1, :1], 'severo'),
                (y[5, :, 1:, :1, :1], 'critico'),
            ]
        ], group='% known active cases by severity') +
        hv.Overlay([
            hv.Curve((T, 100 * yi.sum(axis=(0, 1, 2, 3)) / y[2:, :, :, :1, :1].sum(axis=(0, 1, 2, 3, 4))),
                     'date', '% by severity', label=name)
            for yi, name in [
                (y[2, :, :, :1, :1], 'asintomatico'),
                (y[3, :, :, :1, :1], 'pauci-lieve'),
                (y[4, :, :, :1, :1], 'severo'),
                (y[5, :, :, :1, :1], 'critico'),
            ]
        ] + [
            hv.VLine(seir.cross_beta.T_MEDRXIV_SURVEY).options(color='grey', alpha=0.5, line_dash='dashed'),
            hv.HLine(seir.cross_beta.PERCENT_ASYMPTOMATIC).options(color='grey', alpha=0.5, line_dash='dashed'),
            hv.HLine(seir.cross_beta.PERCENT_ASYMPTOMATIC - 2 * seir.cross_beta.SD_ASYMPTOMATIC)
        .options(color='grey', alpha=0.3, line_dash='dotted'),
            hv.HLine(seir.cross_beta.PERCENT_ASYMPTOMATIC + 2 * seir.cross_beta.SD_ASYMPTOMATIC)
        .options(color='grey', alpha=0.3, line_dash='dotted'),
        ], group='% all active cases by severity') +
        hv.Overlay([
            hv.Curve((T, 100 * yi.sum(axis=(0, 1, 2, 3)) / y[:, :, 1:, :, :].sum(axis=(0, 1, 2, 3, 4))),
                     'date', '% cases by age', label=name) *
            hv.Scatter(seir.cross_beta.cases_by_age, 'day', name, label=name).options(size=6, alpha=0.4)
            for yi, name in [
                (y[:, 0, 1:, :, :], '0-50'),
                (y[:, 1, 1:, :, :], '51-70'),
                (y[:, 2, 1:, :, :], '>70'),
            ]
        ], group='% by age').redim.range(**{'% cases by age': (0, 100)})
    ).cols(1)

In [51]:
%%opts Overlay [aspect=3]

with open('tmp.pkl', 'rb') as f:
    kwargs = pickle.load(f)

plot(kwargs)

:Layout
   .Overlay.I                                :Overlay
      .Curve.Totale_casi              :Curve   [date]   (Count)
      .Scatter.Totale_casi            :Scatter   [data]   (totale_casi)
      .Curve.Totale_positivi          :Curve   [date]   (Count)
      .Scatter.Totale_positivi        :Scatter   [data]   (totale_positivi)
      .Curve.Deceduti                 :Curve   [date]   (Count)
      .Scatter.Deceduti               :Scatter   [data]   (deceduti)
      .Curve.Isolamento_domiciliare   :Curve   [date]   (Count)
      .Scatter.Isolamento_domiciliare :Scatter   [data]   (isolamento_domiciliare)
      .Curve.Ricoverati_con_sintomi   :Curve   [date]   (Count)
      .Scatter.Ricoverati_con_sintomi :Scatter   [data]   (ricoverati_con_sintomi)
      .Curve.Terapia_intensiva        :Curve   [date]   (Count)
      .Scatter.Terapia_intensiva      :Scatter   [data]   (terapia_intensiva)
      .Curve.Dimessi_guariti          :Curve   [date]   (Count)
      .Scatter.Dimessi_guariti        :Scatter   [data]   (dimessi_guariti)
      .Curve.Hidden_cases             :Curve   [date]   (Count)
      .Curve.All_cases                :Curve   [date]   (Count)
   .Overlay.II                               :Overlay
      .Curve.Totale_casi              :Curve   [date]   (Count)
      .Scatter.Totale_casi            :Scatter   [data]   (totale_casi)
      .Curve.Totale_positivi          :Curve   [date]   (Count)
      .Scatter.Totale_positivi        :Scatter   [data]   (totale_positivi)
      .Curve.Deceduti                 :Curve   [date]   (Count)
      .Scatter.Deceduti               :Scatter   [data]   (deceduti)
      .Curve.Isolamento_domiciliare   :Curve   [date]   (Count)
      .Scatter.Isolamento_domiciliare :Scatter   [data]   (isolamento_domiciliare)
      .Curve.Ricoverati_con_sintomi   :Curve   [date]   (Count)
      .Scatter.Ricoverati_con_sintomi :Scatter   [data]   (ricoverati_con_sintomi)
      .Curve.Terapia_intensiva        :Curve   [date]   (Count)
      .Scatter.Terapia_intensiva      :Scatter   [data]   (terapia_intensiva)
      .Curve.Dimessi_guariti          :Curve   [date]   (Count)
      .Scatter.Dimessi_guariti        :Scatter   [data]   (dimessi_guariti)
      .Curve.Hidden_cases             :Curve   [date]   (Count)
      .Curve.All_cases                :Curve   [date]   (Count)
   .Deaths.I                                 :Overlay
      .Curve.A_0_hyphen_minus_50    :Curve   [date]   (count)
      .Scatter.A_0_hyphen_minus_50  :Scatter   [day]   (0-50)
      .Curve.A_51_hyphen_minus_70   :Curve   [date]   (count)
      .Scatter.A_51_hyphen_minus_70 :Scatter   [day]   (51-70)
      .Curve.Greater_than_70        :Curve   [date]   (count)
      .Scatter.Greater_than_70      :Scatter   [day]   (>70)
   .Percent_lethality_by_age.I               :Overlay
      .Curve.A_0_hyphen_minus_50    :Curve   [date]   (% lethality by age)
      .Scatter.A_0_hyphen_minus_50  :Scatter   [x]   (y)
      .Curve.A_51_hyphen_minus_70   :Curve   [date]   (% lethality by age)
      .Scatter.A_51_hyphen_minus_70 :Scatter   [x]   (y)
      .Curve.Greater_than_70        :Curve   [date]   (% lethality by age)
      .Scatter.Greater_than_70      :Scatter   [x]   (y)
   .Percent_known_active_cases_by_severity.I :Overlay
      .Curve.Asintomatico               :Curve   [date]   (% by severity)
      .Scatter.Asintomatico             :Scatter   [day]   (asintomatico)
      .Curve.Pauci_hyphen_minus_lieve   :Curve   [date]   (% by severity)
      .Scatter.Pauci_hyphen_minus_lieve :Scatter   [day]   (pauci-lieve)
      .Curve.Severo                     :Curve   [date]   (% by severity)
      .Scatter.Severo                   :Scatter   [day]   (severo)
      .Curve.Critico                    :Curve   [date]   (% by severity)
      .Scatter.Critico                  :Scatter   [day]   (critico)
   .Percent_all_active_cases_by_severity.I   :Overlay
      .Curve.Asintomatico             :Curve   [date]   (% by severity)
      .Curve.Pauci_hyp

In [31]:
i0 = kwargs['i0']
e0 = np.exp(kwargs['e0'])
beta = np.exp(kwargs['beta'])
beta_detected_ratio = (np.tanh(kwargs['beta_detected_ratio']) + 1) / 2
beta_era_ratios = (np.tanh(kwargs['beta_era_ratios']) + 1) / 2
sigma = np.exp(kwargs['sigma'])
theta = np.exp(kwargs['theta'])
gamma = np.exp(kwargs['gamma'])
mu = np.exp(kwargs['mu'])

print(beta_era_ratios.squeeze())

y = seir.cross_beta.deterministic_ode(i0, e0, beta, beta_detected_ratio, beta_era_ratios, sigma, theta, gamma, mu)

beta = np.concatenate(
    (beta, beta * beta_detected_ratio), axis=3
)
beta_era_ratios = np.concatenate(
    (np.ones_like(beta_era_ratios[..., :1]), beta_era_ratios), axis=-1
)
beta = beta * beta_era_ratios[..., seir.cross_beta.ERA_INDICES]

[0.9999995 0.9865282]


In [32]:
newly_exposed = y[0, :, None, None, ...] * y[None, 2:, :, :, :1, :1] * beta / POPULATION

plots = {}
ages = ['0-50', '51-70', '>70']
symptoms = ['asymptomatic', 'light', 'severe', 'critical']
for (i, agei), (j, agej), (k, symptom), (m, detected) in product(
    enumerate(ages),
    enumerate(ages),
    enumerate(symptoms),
    enumerate([False, True]),
):
    plots[(agei, agej, symptom, detected)] = (
        hv.Curve((seir.cross_beta.T, newly_exposed[i, k, j, m, 0, 0, :]), 'date', 'new infections')
        .options(logy=True)
        .redim.range(**{'new infections': (1, None)})
    )

hv.GridSpace(hv.HoloMap(plots, ['agei', 'agej', 'symptom', 'detected']).overlay(['symptom', 'detected']))

:GridSpace   [agei,agej]
   :NdOverlay   [symptom,detected]
      :Curve   [date]   (new infections)

In [33]:
def sum_but_last(x):
    return np.sum(x, axis=tuple(range(x.ndim-1)))

In [34]:
newly_exposed = y[0, :, None, None, ...] * y[None, 2:, :, :, :1, :1] * beta / POPULATION

plots = {}
ages = ['0-50', '51-70', '>70']
symptoms = ['asymptomatic', 'light', 'severe', 'critical']
for (i, agei), (j, agej) in product(
    enumerate(ages),
    enumerate(ages),
):
    plots[(agei, agej)] = (
        hv.Curve((seir.cross_beta.T, sum_but_last(newly_exposed[i, :, j, :, 0, 0])), 'date', 'new infections')
        .options(logy=True)
        .redim.range(**{'new infections': (1, None)})
    )

hv.GridSpace(hv.HoloMap(plots, ['agei', 'agej']))

:GridSpace   [agei,agej]
   :Curve   [date]   (new infections)

In [35]:
progressions = y[1:-1, ...] * sigma

plots = {}
for (i, age), (j, symptom) in product(
    enumerate(ages),
    enumerate(symptoms),
):
    plots[(age, symptom)] = (
        hv.Curve((seir.cross_beta.T, sum_but_last(progressions[j, i, :, 0, 0])), 'date', 'new progressions')
        .options(logy=True)
        .redim.range(**{'new progressions': (1, None)})
    )

hv.GridSpace(hv.HoloMap(plots, ['age', 'symptom']))

:GridSpace   [age,symptom]
   :Curve   [date]   (new progressions)

In [36]:
recoveries = y[3:, :, :, 0, 0] * gamma

plots = {}
for (i, age), (j, symptom) in product(
    enumerate(ages),
    enumerate(symptoms[1:]),
):
    plots[(age, symptom)] = (
        hv.Curve((seir.cross_beta.T, sum_but_last(recoveries[j, i, :, 0, 0])), 'date', ('y', 'new recoveries'))
        .options(logy=True)
        .redim.range(y=(1, None))
    )

hv.GridSpace(hv.HoloMap(plots, ['age', 'symptom']))

:GridSpace   [age,symptom]
   :Curve   [date]   (y)

In [37]:
recoveries = y[1:, :, :, 0, 0] * gamma

plots = {}
for (i, age), (j, symptom) in product(
    enumerate(ages),
    enumerate(['exposed', 'asymptomatic', 'light', 'severe', 'critical']),
):
    plots[(age, symptom)] = (
        hv.Curve((seir.cross_beta.T, sum_but_last(recoveries[j, i, :, 0, 0])), 'date', ('y', 'new recoveries'))
        .options(logy=True)
        .redim.range(y=(1, None))
    )

hv.GridSpace(hv.HoloMap(plots, ['age', 'symptom']))

:GridSpace   [age,symptom]
   :Curve   [date]   (y)

In [38]:
detections = y[1:, :, :1, :1, :1] * theta

plots = []
for i, symptom in enumerate(['exposed', 'asymptomatic', 'light', 'severe', 'critical']):
    plots.append(
        hv.Curve((seir.cross_beta.T, sum_but_last(detections[i, :, 0, 0, 0])), 'date', ('y', 'new detections'),
                 group=str(symptom))
        .options(logy=True)
        .redim.range(y=(1, None))
    )

hv.Layout(plots).cols(1)

:Layout
   .Exposed.I      :Curve   [date]   (y)
   .Asymptomatic.I :Curve   [date]   (y)
   .Light.I        :Curve   [date]   (y)
   .Severe.I       :Curve   [date]   (y)
   .Critical.I     :Curve   [date]   (y)

In [39]:
deaths = y[3:, :, :, :1, :1] * mu

plots = {}
for (i, age), (j, symptom), (k, detected) in product(
    enumerate(ages),
    enumerate(['light', 'severe', 'critical']),
    enumerate(['False', 'True']),
):
    plots[(age, symptom, detected)] = (
        hv.Curve((seir.cross_beta.T, sum_but_last(deaths[j, i, k, 0, 0])), 'date', ('y', 'new deaths'))
        .options(logy=True)
        .redim.range(y=(1, None))
    )

hv.GridSpace(hv.HoloMap(plots, ['age', 'symptom', 'detected']).overlay('detected'))

:GridSpace   [age,symptom]
   :NdOverlay   [detected]
      :Curve   [date]   (y)

In [40]:
import theano.tensor as tt

In [41]:
tt.Tensor('float64', [True, True, True, True])()[None, 0, 0, :1, :].broadcastable

ValueError: Cannot compute test value: input 0 (<TensorType(float64, (True, True, True, True))>) of Op InplaceDimShuffle{x,0,1,2,3}(<TensorType(float64, (True, True, True, True))>) missing default value.  
Backtrace when that variable is created:

  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/site-packages/ipykernel/zmqshell.py", line 536, in run_cell
    return super(ZMQInteractiveShell, self).run_cell(*args, **kwargs)
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 2858, in run_cell
    raw_cell, store_history, silent, shell_futures)
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 2886, in _run_cell
    return runner(coro)
  File "/Users/robertperrotta/miniconda3/envs/pymc3ode/lib/python3.7/site-packages/IPython/core/async_helpers.py", line 68, in _pseudo_sync_runner
    coro.send(None)
  File "/Users/robertperrot

In [ ]:
with pm.Model() as model:
    
    x = pm.Normal('x', shape=(2, 3, 4))
    
x.broadcastable